In [6]:
import numpy as np
from scipy.io import wavfile

In [7]:
import IPython

# Creating Note Frequencies

In [8]:
octave=['C', 'c', 'D', 'd', 'E', 'F', 'f', 'G', 'g', 'A', 'a', 'B']
base_freq=440
keys=np.array([x+str(y) for y in range(0,9) for x in octave])
start = np.where(keys == 'A0')[0][0]
end = np.where(keys == 'C8')[0][0]
keys = keys[start:end+1]
note_freqs = dict(zip(keys, [2**((n+1-49)/12)*base_freq for n in range(len(keys))]))
note_freqs[''] = 0.0

In [9]:
def get_sine_wave(frequency, duration, sample_rate=44100, amplitude=4096):
    t = np.linspace(0, duration, int(sample_rate*duration)) # Time axis
    wave = amplitude*np.sin(2*np.pi*frequency*t)
    return wave

In [13]:

factor=[i/10 for i in np.logspace(1,0,5)]


def apply_overtones(frequency, duration, factor, sample_rate=44100, amplitude=4096):
    freq=[frequency*i for i in range(1,5)]
    frequencies = np.minimum(np.array([frequency*(x+1) for x in range(len(factor))]), sample_rate//2)
    amplitudes = np.array([amplitude*x for x in factor])
    
    fundamental = get_sine_wave(frequencies[0], duration, sample_rate, amplitudes[0])
    for i in range(1, len(factor)):
        overtone = get_sine_wave(frequencies[i], duration, sample_rate, amplitudes[i])
        fundamental += overtone
    return fundamental



In [29]:
def get_adsr_weights(frequency, duration, length, decay, sustain_level, sample_rate=44100):

    #assert abs(sum(length)-1) < 1e-8
    assert len(length) ==len(decay) == 4
    
    intervals = int(duration*frequency)
    len_A = np.maximum(int(intervals*length[0]),1)
    len_D = np.maximum(int(intervals*length[1]),1)
    len_S = np.maximum(int(intervals*length[2]),1)
    len_R = np.maximum(int(intervals*length[3]),1)
    
    decay_A = decay[0]
    decay_D = decay[1]
    decay_S = decay[2]
    decay_R = decay[3]
    
    A = 1/np.array([(1-decay_A)**n for n in range(len_A)])
    A = A/np.nanmax(A)
    D = np.array([(1-decay_D)**n for n in range(len_D)])
    D = D*(1-sustain_level)+sustain_level
    S = np.array([(1-decay_S)**n for n in range(len_S)])
    S = S*sustain_level
    R = np.array([(1-decay_R)**n for n in range(len_R)])
    R = R*S[-1]
    
    weights = np.concatenate((A,D,S,R))
    len(weights)
    smoothing = np.array([0.1*(1-0.1)**n for n in range(5)])
    smoothing = smoothing/np.nansum(smoothing)
    weights = np.convolve(weights, smoothing, mode='same')
    
    weights = np.repeat(weights, int(sample_rate*duration/intervals))
    tail = int(sample_rate*duration-weights.shape[0])
    if tail > 0:
        weights = np.concatenate((weights, weights[-1]-weights[-1]/tail*np.arange(tail)))
    return weights

In [30]:

#note = apply_overtones(frequency, duration=2.5, factor=factor)
IPython.display.Audio(note,rate=44100)

In [37]:
def get_note(frequency,duration=2.5, adsr_length_ratio=[0.05, 0.25, 0.55, 0.9], adsr_decay=[0.075,0.04,0.01,0.1], adsr_sustain=0.2):
    note = apply_overtones(frequency, duration, factor=factor)
    adsr_length=[i*duration for i in adsr_length_ratio]
    print(adsr_length)
    weights = get_adsr_weights(frequency, duration, adsr_length, adsr_decay, adsr_sustain)
    note=note*weights
    note = note*(4096/np.max(note))
    return note

In [38]:
import matplotlib.pyplot as plt

In [39]:
plt.style.use('seaborn-dark')
note_a=get_note(note_freqs['C4'], 10)
note_b=get_note(note_freqs['D4'])
note=np.append(note_a,note_b)
IPython.display.Audio(note,rate=44100)

[0.5, 2.5, 5.5, 9.0]


ValueError: operands could not be broadcast together with shapes (441000,) (7691040,) 

In [154]:
import numpy as np
from scipy.io import wavfile
import IPython
class note_manager:
    def __init__(self):
        # Map notes to frequencies
        octave=['C', 'c', 'D', 'd', 'E', 'F', 'f', 'G', 'g', 'A', 'a', 'B']
        self.base_freq=440
        keys=np.array([x+str(y) for y in range(0,9) for x in octave])
        start = np.where(keys == 'A0')[0][0]
        end = np.where(keys == 'C8')[0][0]
        keys = keys[start:end+1]
        self.note_freqs = dict(zip(keys, [2**((n+1-49)/12)*self.base_freq for n in range(len(keys))]))
        self.note_freqs[''] = 0.0
        self.factor=[i/10 for i in np.logspace(1,0,5)]
        self.sample_rate=44100
        #
    def get_sine_wave(self,frequency, duration, sample_rate=44100, amplitude=4096):
        t = np.linspace(0, duration, int(sample_rate*duration)) # Time axis
        wave = amplitude*np.sin(2*np.pi*frequency*t)
        print(wave.shape)
        return wave
      
    def apply_overtones(self,frequency, duration, factor, sample_rate=44100, amplitude=4096):
        freq=[frequency*i for i in range(1,5)]
        frequencies = np.minimum(np.array([frequency*(x+1) for x in range(len(factor))]), sample_rate//2)
        amplitudes = np.array([amplitude*x for x in factor])
        
        fundamental = self.get_sine_wave(frequencies[0], duration, sample_rate, amplitudes[0])
        for i in range(1, len(factor)):
            overtone = self.get_sine_wave(frequencies[i], duration, sample_rate, amplitudes[i])
            fundamental += overtone
        return fundamental

    def get_adsr_weights(self,frequency, duration, length, decay, sustain_level, sample_rate=44100):

        assert abs(sum(length)-1) < 1e-8
        assert len(length) ==len(decay) == 4
        
        intervals = int(duration*frequency)
        print(intervals)
        len_A = np.maximum(int(intervals*length[0]),1)
        len_D = np.maximum(int(intervals*length[1]),1)
        len_S = np.maximum(int(intervals*length[2]),1)
        len_R = np.maximum(int(intervals*length[3]),1)
        
        decay_A = decay[0]
        decay_D = decay[1]
        decay_S = decay[2]
        decay_R = decay[3]
        
        A = 1/np.array([(1-decay_A)**n for n in range(len_A)])
        A = A/np.nanmax(A)
        D = np.array([(1-decay_D)**n for n in range(len_D)])
        D = D*(1-sustain_level)+sustain_level
        S = np.array([(1-decay_S)**n for n in range(len_S)])
        S = S*sustain_level
        R = np.array([(1-decay_R)**n for n in range(len_R)])
        R = R*S[-1]
        
        weights = np.concatenate((A,D,S,R))
        
        smoothing = np.array([0.1*(1-0.1)**n for n in range(5)])
        smoothing = smoothing/np.nansum(smoothing)
        weights = np.convolve(weights, smoothing, mode='same')
        print(weights)
        weights = np.repeat(weights, int(sample_rate*duration/len(weights)))
        print(len(weights))
        tail = int(sample_rate*duration-weights.shape[0])
        if tail > 0:
            weights = np.concatenate((weights, weights[-1]-weights[-1]/tail*np.arange(tail)))
        return weights

    def get_note(self,frequency,duration=2.5):
        
        note = self.apply_overtones(frequency, duration, factor=self.factor)
        weights = self.get_adsr_weights(frequency, duration, length=[0.05, 0.25, 0.55, 0.15],
                                decay=[0.075,0.04,0.01,0.1], sustain_level=0.2)
        print(note.shape)
        print(weights.shape)
        note=note*weights
        note = note*(4096/np.max(note))
        return note

    def make_music(self,frequencies_dict):
        music=np.array([0])
        for freq,time in frequencies_dict.items():
            print(freq,time)
            note=self.get_note(freq,time)
            music=np.append(music,note)
            
        wavfile.write('music.wav', rate=self.sample_rate, data=music.astype(np.int16))
        return music

In [103]:
# create a frequencies dictionary

In [4]:
pip install opencv-python

     --------------------------------------- 35.6/35.6 MB 19.8 MB/s eta 0:00:00
Note: you may need to restart the kernel to use updated packages.


In [7]:
from PIL import Image

In [9]:
im = Image.open('web_first_images_release.png').convert('RGB')
r, g, b = im.split()

In [15]:
import numpy as np

In [16]:
na = np.array(im).astype(np.float)
red=na[...,0]

C:\Users\umang\AppData\Local\Temp\ipykernel_24896\3829156403.py:1: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  na = np.array(im).astype(np.float)


In [157]:

red=red.flatten()
r_max=red.max()
threshold=0.5*r_max
total_len=len(red)

temp=[i if i>=threshold else 0 for i in red]    

In [158]:
red[0]

24.0

In [159]:
from collections import OrderedDict

d=OrderedDict()
prev=0
s=0
for i in temp:
    if i==0:
        s+=1
    else:
        d[prev]=s
        prev=i
        s=0

d=list(d.items())

In [160]:
freq=OrderedDict()
index=0
n=len(d)
while True and index<n:
    k,v=d[index]
    if v!=0:
        freq[k]=v
        index+=1
        continue
    else:
        i=index
        temp=[]
        k_temp,v_temp=k,v
        while v_temp==0 and i<n:
            temp.append(d[i])
            v_temp=d[i][1]
            i+=1
        #temp.append(d[i+1])
        index=i+2
        k_avg=sum([k for k,v in temp])/len(temp)
        v=temp[-1][1]
        freq[k_avg]=v
        continue

freq=list(freq.items())

In [161]:
freq

[(0, 40),
 (183.11764705882354, 102),
 (204.33333333333334, 45),
 (164.0, 72),
 (179.33333333333334, 357),
 (171.875, 244),
 (158.5, 356),
 (150.5, 23),
 (186.75, 50),
 (185.8181818181818, 23),
 (192.3846153846154, 22),
 (216.5, 27),
 (225.16666666666666, 0)]

In [162]:
frequencies=[k for k,v in freq]
times=[v for k,v in freq]


In [163]:
max_times=max(times)
min_times=min(times)
maximum_time_threshold=10
times=[((i-min_times)*maximum_time_threshold)/(max_times-min_times) for i in times]

In [164]:
note_min=27.5
note_max=4186.009044809578
max_freq=max(frequencies)
min_freq=min(frequencies)
frequencies=[((i-min_freq)/(max_freq-min_freq))*(note_max-note_min)+note_min for i in frequencies]

In [168]:
music=OrderedDict()
for f,t in zip(frequencies,times):
    if t!=0:
        music[f-1000]=round(t,2)

In [169]:
music

OrderedDict([(-972.5, 1.12),
             (2409.423278571572, 2.86),
             (2801.246920012245, 1.26),
             (2056.3474464046076, 2.02),
             (2339.532370255445, 10.0),
             (2201.7875295779995, 6.83),
             (1954.7702454581113, 9.97),
             (1807.0215895359356, 0.64),
             (2476.5076866832956, 1.4),
             (2459.2983261923605, 0.64),
             (2580.5710428977127, 0.62),
             (3025.9480008938876, 0.76)])

In [170]:
manager=note_manager()
music1={440:5}
t=manager.make_music(music)
IPython.display.Audio(t,rate=44100)

-972.5 1.12
(49392,)
(49392,)
(49392,)
(49392,)
(49392,)
-1089
[0.46396913 0.46641108 0.46860883 0.42174794 0.23537887]
49390
(49392,)
(49392,)
2409.423278571572 2.86
(126126,)
(126126,)
(126126,)
(126126,)
(126126,)
6890
[1.75559121e-12 2.33152454e-12 2.91079635e-12 ... 4.28669284e-65
 3.08641884e-65 2.08333272e-65]
123984
(126126,)
(126126,)
2801.246920012245 1.26
(55566,)
(55566,)
(55566,)
(55566,)
(55566,)
3529
[8.56273095e-07 1.13717916e-06 1.41971353e-06 ... 5.81330082e-34
 4.18557659e-34 2.82526420e-34]
52905
(55566,)
(55566,)
2056.3474464046076 2.02
(89082,)
(89082,)
(89082,)
(89082,)
(89082,)
4153
[7.63846359e-08 1.01443122e-07 1.26646863e-07 ... 1.01737981e-39
 7.32513466e-40 4.94446590e-40]
87171
(89082,)
(89082,)
2339.532370255445 10.0
(441000,)
(441000,)
(441000,)
(441000,)
(441000,)
23395
[2.04810825e-040 2.72000373e-040 3.39579396e-040 ... 5.16264537e-218
 3.71710467e-218 2.50904565e-218]
421074
(441000,)
(441000,)
2201.7875295779995 6.83
(301203,)
(301203,)
(301203,)
(3